In [528]:
import numpy as np
import pandas as pd
import pickle

from tqdm import tqdm

import mesa

import seaborn as sns

from scipy.stats import genextreme

In [301]:
#########################
# LOAD WORLD RISK INDEX DATA
#########################

wri = pd.read_excel("data/WRI_FullData_Time-series-2000-2022.xlsx", sheet_name=None)
del wri["Codes"]

data = []
for k,v in wri.items():
    year = k.split()[-1]
    vals = v.copy()
    #Removing all composite KPI's
    vals = vals[["Country", "Code",
                 "EI_02b", "EI_02d", "EI_02f", "EI_03b", "EI_03d", "EI_03f", "EI_05b", "EI_05d", "EI_05f", "EI_07b",
                 "SI_01a", "SI_02b", "SI_02a", "SI_03a", "SI_05a", "SI_08a", "SI_12b", "SI_13b", 
                 "CI_01b", "CI_05b", 
                 "AI_01a", "AI_02a"]]
    vals.insert(loc=0,column="Year",value=year)

    data.append(vals)
    #wri_df = wri_df.merge(v, on="Country", how="inner")
wri_df = pd.concat(data, ignore_index=True)
wri_df["Year"] = wri_df["Year"].astype(int)
wri_df.rename(columns={"Code":"ISO"},inplace=True)
wri_columns = wri_df.columns[2:-1]

In [300]:
#########################
# LOAD POPULATION DENSITY DATA
#########################

size = pd.read_csv("data/country_size.csv")
size = size.drop(["Country Name", "Indicator Name", "Indicator Code"],axis=1)
size = pd.melt(size, id_vars=['Country Code'], var_name='Year', value_name='Value')
size.rename(columns={"Country Code":"ISO", "Value":"Size"},inplace=True)
size = size.dropna()
size["Year"] = size["Year"].astype(int)

In [315]:
country_regions = pd.read_csv("data/model_params/countries_regions.csv")

countries = country_regions["Country"].unique()
regions = country_regions["Region"].unique()

In [332]:
occurences_params = pd.read_csv("data/model_params/occurences_countries_trending.csv")
outlier_prop_params = pd.read_csv("data/model_params/region_proportions_betadist.csv")

disaster_params_trending = pd.read_csv("data/model_params/disaster_magnitudes_trending.csv")
disaster_params_stationary = pd.read_csv("data/model_params/disaster_magnitudes_stationary.csv")

displacement_reg_params = pd.read_csv("data/model_params/displacement_regression.csv")

In [333]:
with open('data/model_params/scaler_flood.pkl', 'rb') as file:
    scaler_flood = pickle.load(file)
with open('data/model_params/factor_analyzer_flood.pkl', 'rb') as file:
    fa_flood = pickle.load(file)
with open('data/model_params/kmeans_flood.pkl', 'rb') as file:
    kmeans_flood = pickle.load(file)
with open('data/model_params/label_probs_floods.pkl', 'rb') as file:
    labelprobs_flood = pickle.load(file)

with open('data/model_params/scaler_storm.pkl', 'rb') as file:
    scaler_storm = pickle.load(file)
with open('data/model_params/factor_analyzer_storm.pkl', 'rb') as file:
    fa_storm = pickle.load(file)
with open('data/model_params/kmeans_storm.pkl', 'rb') as file:
    kmeans_storm = pickle.load(file)
with open('data/model_params/label_probs_storms.pkl', 'rb') as file:
    labelprobs_storm = pickle.load(file)

# Model

describe math here

In [631]:
class CountryAgent(mesa.Agent):
    """An agent with fixed initial wealth."""

    def __init__(self, unique_id, model):
        # Pass the parameters to the parent class.
        super().__init__(unique_id, model)

        # Create the agent's variable and set the initial values.
        self.country_iso = countries[unique_id]
        self.region = country_regions[country_regions["Country"] == self.country_iso]["Region"].iloc[0]


        self.size = size[(size["ISO"] == self.country_iso) & (size["Year"] == self.model.year)]["Size"].iloc[0]

        self.wri = wri_df[(wri_df["ISO"] == self.country_iso) & (wri_df["Year"] == self.model.year)].drop(["Country","ISO"],axis=1)

        ##### Disaster occurences parameters ######
        # Number of disasters
        self.flood_occurences_alpha = occurences_params[occurences_params["Country"] == self.country_iso]["Alpha_flood_occurences"].iloc[0]
        self.flood_occurences_beta = occurences_params[occurences_params["Country"] == self.country_iso]["Beta_flood_occurences"].iloc[0]
        self.storm_occurences_alpha = occurences_params[occurences_params["Country"] == self.country_iso]["Alpha_storm_occurences"].iloc[0]
        self.storm_occurences_beta = occurences_params[occurences_params["Country"] == self.country_iso]["Beta_storm_occurences"].iloc[0]

        # Flood outlier proportions
        self.flood_outlierprop_alpha = outlier_prop_params[outlier_prop_params["Region"] == self.region]["Alpha_Flood"].iloc[0]
        self.flood_outlierprop_beta = outlier_prop_params[outlier_prop_params["Region"] == self.region]["Beta_Flood"].iloc[0]
        # Storm outlier proportions
        self.storm_outlierprop_alpha = outlier_prop_params[outlier_prop_params["Region"] == self.region]["Alpha_Storm"].iloc[0]
        self.storm_outlierprop_beta = outlier_prop_params[outlier_prop_params["Region"] == self.region]["Beta_Storm"].iloc[0]

        
        ##### Stationary Disaster parameters ######
        # Flood Duration
        self.flood_outlier_duration_shape = disaster_params_stationary[(disaster_params_stationary["Region"] == self.region) & (disaster_params_stationary["Var"] == "Flood_outlier_duration")]["Shape"].iloc[0]
        self.flood_outlier_duration_scale = disaster_params_stationary[(disaster_params_stationary["Region"] == self.region) & (disaster_params_stationary["Var"] == "Flood_outlier_duration")]["Scale"].iloc[0]
        self.flood_outlier_duration_location = disaster_params_stationary[(disaster_params_stationary["Region"] == self.region) & (disaster_params_stationary["Var"] == "Flood_nonoutlier_duration")]["Location"].iloc[0]
        self.flood_nonoutlier_duration_shape = disaster_params_stationary[(disaster_params_stationary["Region"] == self.region) & (disaster_params_stationary["Var"] == "Flood_nonoutlier_duration")]["Shape"].iloc[0]
        self.flood_nonoutlier_duration_scale = disaster_params_stationary[(disaster_params_stationary["Region"] == self.region) & (disaster_params_stationary["Var"] == "Flood_nonoutlier_duration")]["Scale"].iloc[0]
        self.flood_nonoutlier_duration_location = disaster_params_stationary[(disaster_params_stationary["Region"] == self.region) & (disaster_params_stationary["Var"] == "Flood_nonoutlier_duration")]["Location"].iloc[0]
        # Storm Magnitude
        self.storm_magnitude_mu = disaster_params_stationary[(disaster_params_stationary["Region"] == self.region) & (disaster_params_stationary["Var"] == "Storm_magnitude")]["Shape"].iloc[0]
        self.storm_magnitude_sigma = disaster_params_stationary[(disaster_params_stationary["Region"] == self.region) & (disaster_params_stationary["Var"] == "Storm_magnitude")]["Scale"].iloc[0]
        # Storm duration non-outlier
        self.storm_nonoutlier_duration_shape = disaster_params_stationary[(disaster_params_stationary["Region"] == self.region) & (disaster_params_stationary["Var"] == "Storm_duration_nonoutlier")]["Shape"].iloc[0]
        self.storm_nonoutlier_duration_scale = disaster_params_stationary[(disaster_params_stationary["Region"] == self.region) & (disaster_params_stationary["Var"] == "Storm_duration_nonoutlier")]["Scale"].iloc[0]
        self.storm_nonoutlier_duration_location = disaster_params_stationary[(disaster_params_stationary["Region"] == self.region) & (disaster_params_stationary["Var"] == "Storm_duration_nonoutlier")]["Location"].iloc[0]
        
        ##### Trending Disaster Parameters ######
        # Flood Magnitudes as functions of T
        self.flood_outlier_magnitude_shape = disaster_params_trending[(disaster_params_trending["Region"] == self.region) & (disaster_params_trending["Var"] == "Flood_magnitude_outlier")]["Shape"].iloc[0]
        self.flood_outlier_magnitude_scale_coef = disaster_params_trending[(disaster_params_trending["Region"] == self.region) & (disaster_params_trending["Var"] == "Flood_magnitude_outlier")]["Scale_coef"].iloc[0]
        self.flood_nonoutlier_magnitude_shape = disaster_params_trending[(disaster_params_trending["Region"] == self.region) & (disaster_params_trending["Var"] == "Flood_magnitude_nonoutlier")]["Shape"].iloc[0]
        self.flood_nonoutlier_magnitude_scale_coef = disaster_params_trending[(disaster_params_trending["Region"] == self.region) & (disaster_params_trending["Var"] == "Flood_magnitude_nonoutlier")]["Scale_coef"].iloc[0]
        # Storm Durations as functions of T
        self.storm_outlier_duration_shape = disaster_params_trending[(disaster_params_trending["Region"] == self.region) & (disaster_params_trending["Var"] == "Storm_duration_outlier")]["Shape"].iloc[0]
        self.storm_outlier_duration_scale_coef = disaster_params_trending[(disaster_params_trending["Region"] == self.region) & (disaster_params_trending["Var"] == "Storm_duration_outlier")]["Scale_coef"].iloc[0]

    def step(self):
        #Assume that all idps from the previous year has been resettled
        self.idp = 0

        self.pop = int(self.model.country_params[(self.model.country_params["country"] == self.country_iso) & (self.model.country_params["time"] == self.model.year)]["population"].iloc[0] * 1000000)
        self.gdp = self.model.country_params[(self.model.country_params["country"] == self.country_iso) & (self.model.country_params["time"] == self.model.year)]["gdp"].iloc[0] * 10000000000
        self.popdens = self.pop / self.size

        self.wri["Year"] = self.model.year - 2000
        self.wri["Popdens"] = self.pop / self.size

        lambda_f = np.exp(self.flood_occurences_alpha + self.flood_occurences_beta*self.model.T)
        lambda_s = np.exp(self.storm_occurences_alpha + self.storm_occurences_beta*self.model.T)

        floods = np.random.poisson(lambda_f)
        self.flood_outcomes = []
        storms = np.random.poisson(lambda_s)
        self.storm_outcomes = []

        if (self.flood_outlierprop_alpha > 0) & (self.flood_outlierprop_beta > 0):
            outlier_prop_flood = np.random.beta(self.flood_outlierprop_alpha, self.flood_outlierprop_beta)
        else:
            outlier_prop_flood = 0
        
        if (self.storm_outlierprop_alpha > 0) & (self.storm_outlierprop_beta > 0):
            outlier_prop_storm = np.random.beta(self.storm_outlierprop_alpha, self.storm_outlierprop_beta)
        else:
            outlier_prop_storm = 0

        # Generate Flood magnitudes and durations
        for i in range(floods):
            dis = self.wri.copy()
            if self.flood_outlier_duration_shape is not None:
                outlier = np.random.binomial(1,outlier_prop_flood)
            else:
                outlier = 0
                print("No outlier distribution")
            if outlier:
                scale = np.exp(self.flood_outlier_magnitude_scale_coef * self.model.T)
                mag = np.random.weibull(self.flood_outlier_magnitude_shape) * scale
                mag = mag - self.model.floodscaler["outliers"]["shiftval"]
                mag = (mag * self.model.floodscaler["outliers"]["std"]) + self.model.floodscaler["outliers"]["mean"]
                duration = np.random.weibull(self.flood_outlier_duration_shape) * self.flood_outlier_duration_scale + self.flood_outlier_duration_location
            else:
                scale = np.exp(self.flood_nonoutlier_magnitude_scale_coef * self.model.T)
                mag = np.random.weibull(self.flood_nonoutlier_magnitude_shape) * scale
                mag = mag - self.model.floodscaler["nonoutliers"]["shiftval"]
                mag = (mag * self.model.floodscaler["nonoutliers"]["std"]) + self.model.floodscaler["nonoutliers"]["mean"]
                duration = np.random.gamma(self.flood_nonoutlier_duration_shape,self.flood_nonoutlier_duration_scale) + self.flood_nonoutlier_duration_location
            #print(f"Flood {i}, outlier={outlier}, magnitude={mag}, duration={duration}")
            dis.insert(loc=1,column="Duration",value=duration)
            dis.insert(loc=1,column="Dis Mag Value",value=mag)
            cluster = kmeans_flood.predict(fa_flood.transform(scaler_flood.transform(dis)))
            
            disp = np.random.binomial(1,labelprobs_flood[cluster[0]][1])
            displacement_vars = np.array([1,mag,duration,self.popdens,self.pop])
            if disp:
                if self.pop < 0:#10000000:
                    pred = sum(displacement_vars * self.model.flood_disp_abs)
                    displacement = int(np.random.normal(pred, self.model.flood_disp_abs_rmse))
                    displacement = max(0,displacement)
                else:
                    pred = sum(displacement_vars * self.model.flood_disp_pct)
                    displacement = max(0,np.random.normal(pred, self.model.flood_disp_pct_rmse))
                    displacement = int(displacement*self.pop)
            else:
                displacement = 0
            self.idp += displacement
            self.pop -= displacement
            self.flood_outcomes.append(np.append(displacement_vars,displacement))

        # Generate Storm magnitudes and durations
        for i in range(storms):
            dis = self.wri.copy()
            mag = np.random.normal(self.storm_magnitude_mu,self.storm_magnitude_sigma)
            outlier = np.random.binomial(1,outlier_prop_storm)
            if outlier:
                scale = np.exp(self.storm_outlier_duration_scale_coef * self.model.T)
                duration = np.random.weibull(self.storm_outlier_duration_shape) * scale
                duration = duration - self.model.stormscaler["shiftval"]
                duration = (duration * self.model.stormscaler["std"]) + self.model.stormscaler["mean"]
            else:
                duration = np.random.gamma(self.storm_nonoutlier_duration_shape,self.storm_nonoutlier_duration_scale) + self.storm_nonoutlier_duration_location
            #print(f"Storm {i}, outlier={outlier}, magnitude={mag}, duration={duration}")
            dis.insert(loc=1,column="Duration",value=duration)
            dis.insert(loc=1,column="Dis Mag Value",value=mag)
            cluster = kmeans_storm.predict(fa_storm.transform(scaler_storm.transform(dis)))

            disp = np.random.binomial(1,labelprobs_storm[cluster[0]][1])
            displacement_vars = np.array([1,mag,duration,self.popdens,self.pop])
            if disp:
                if self.pop < 0:#10000000:
                    pred = sum(displacement_vars * self.model.storm_disp_abs)
                    displacement = int(np.random.normal(pred, self.model.storm_disp_abs_rmse))
                    displacement = max(0,displacement)
                else:
                    pred = sum(displacement_vars * self.model.storm_disp_pct)
                    displacement = max(0,np.random.normal(pred, self.model.storm_disp_pct_rmse))
                    displacement = int(displacement*self.pop)
            else:
                displacement = 0
            self.idp += displacement
            self.pop -= displacement
            self.storm_outcomes.append(np.append(displacement_vars,displacement))

        #print(f"Hi, I am {countries[self.unique_id]} from {self.region}, my population is {self.pop} and my gdp is {self.gdp}. I have experienced {floods} floods and {storms} storms this year, which displaced {self.idp} people")


In [611]:
def flood_data(model):
    floods = [agent.flood_outcomes for agent in model.schedule.agents]
    num_floods = sum(len(arr) for entry in floods for arr in entry)
    flood_idps = sum([sum(arr[-1] for arr in entry) for entry in floods])
    flood_mag = round(np.mean([arr[1] for entry in floods for arr in entry]),2)
    flood_dur = round(np.mean([arr[2] for entry in floods for arr in entry]),2)
    flood_results = {"Num":num_floods, "idps":flood_idps, "avg_mag":flood_mag, "avg_dur":flood_dur}
    return flood_results

def storm_data(model):
    storms = [agent.storm_outcomes for agent in model.schedule.agents]
    num_storms = sum(len(arr) for entry in storms for arr in entry)
    storm_idps = sum([sum(arr[-1] for arr in entry) for entry in storms])
    storm_mag = round(np.mean([arr[1] for entry in storms for arr in entry]),2)
    storm_dur = round(np.mean([arr[2] for entry in storms for arr in entry]),2)
    storm_results = {"Num":num_storms, "idps":storm_idps, "avg_mag":storm_mag, "avg_dur":storm_dur}
    return storm_results

class DisplacementModel(mesa.Model):
    """A model with some number of agents."""
    
    def __init__(self, countries, scenario="SSP119", start_year=2020, end_year=2300):
        # Load scenario data
        self.global_params = pd.read_csv("data/env_params/"+scenario+"/global_params.csv")
        self.country_params = pd.read_csv("data/env_params/"+scenario+"/country_params.csv")

        # Create scheduler and assign it to the model
        self.schedule = mesa.time.RandomActivation(self)

        self.year = start_year
        self.T = self.global_params[self.global_params["time"] == self.year]["T"].iloc[0]
        self.floodscaler = {}
        self.floodscaler["outliers"] = {}
        self.floodscaler["nonoutliers"] = {}
        self.floodscaler["outliers"]["mean"] = disaster_params_trending[disaster_params_trending["Var"] == "Flood_magnitude_outliers_scalermean"]["Shape"].iloc[0]
        self.floodscaler["outliers"]["std"] = disaster_params_trending[disaster_params_trending["Var"] == "Flood_magnitude_outliers_scalerstd"]["Shape"].iloc[0]
        self.floodscaler["outliers"]["shiftval"] = disaster_params_trending[disaster_params_trending["Var"] == "Flood_magnitude_outliers_scalershiftval"]["Shape"].iloc[0]
        self.floodscaler["nonoutliers"]["mean"] = disaster_params_trending[disaster_params_trending["Var"] == "Flood_magnitude_nonoutliers_scalermean"]["Shape"].iloc[0]
        self.floodscaler["nonoutliers"]["std"] = disaster_params_trending[disaster_params_trending["Var"] == "Flood_magnitude_nonoutliers_scalerstd"]["Shape"].iloc[0]
        self.floodscaler["nonoutliers"]["shiftval"] = disaster_params_trending[disaster_params_trending["Var"] == "Flood_magnitude_nonoutliers_scalershiftval"]["Shape"].iloc[0]

        self.stormscaler = {}
        self.stormscaler["mean"] = disaster_params_trending[disaster_params_trending["Var"] == "Storm_duration_outliers_scalermean"]["Shape"].iloc[0]
        self.stormscaler["std"] = disaster_params_trending[disaster_params_trending["Var"] == "Storm_duration_outliers_scalerstd"]["Shape"].iloc[0]
        self.stormscaler["shiftval"] = disaster_params_trending[disaster_params_trending["Var"] == "Storm_duration_outliers_scalershiftval"]["Shape"].iloc[0]

        self.storm_displacement = displacement_reg_params[displacement_reg_params["Model"] == "Storm_disp"]
        self.flood_displacement = displacement_reg_params[displacement_reg_params["Model"] == "Flood_disp"]

        #Regression models for displacement
        self.flood_disp_abs_rmse = displacement_reg_params[displacement_reg_params["Model"] == "Flood_disp_abs"]["rmse"].iloc[0]
        self.flood_disp_abs = np.array([displacement_reg_params[displacement_reg_params["Model"] == "Flood_disp_abs"]["Intercept"].iloc[0],
                                        displacement_reg_params[displacement_reg_params["Model"] == "Flood_disp_abs"]["Dis Mag Value"].iloc[0],
                                        displacement_reg_params[displacement_reg_params["Model"] == "Flood_disp_abs"]["Duration"].iloc[0],
                                        displacement_reg_params[displacement_reg_params["Model"] == "Flood_disp_abs"]["Popdens"].iloc[0],
                                        displacement_reg_params[displacement_reg_params["Model"] == "Flood_disp_abs"]["Pop"].iloc[0]])
        
        self.flood_disp_pct_rmse = displacement_reg_params[displacement_reg_params["Model"] == "Flood_disp_pct"]["rmse"].iloc[0]
        self.flood_disp_pct = np.array([displacement_reg_params[displacement_reg_params["Model"] == "Flood_disp_pct"]["Intercept"].iloc[0],
                                        displacement_reg_params[displacement_reg_params["Model"] == "Flood_disp_pct"]["Dis Mag Value"].iloc[0],
                                        displacement_reg_params[displacement_reg_params["Model"] == "Flood_disp_pct"]["Duration"].iloc[0],
                                        displacement_reg_params[displacement_reg_params["Model"] == "Flood_disp_pct"]["Popdens"].iloc[0],0])
        
        self.storm_disp_abs_rmse = displacement_reg_params[displacement_reg_params["Model"] == "Storm_disp_abs"]["rmse"].iloc[0]
        self.storm_disp_abs = np.array([displacement_reg_params[displacement_reg_params["Model"] == "Storm_disp_abs"]["Intercept"].iloc[0],
                                        displacement_reg_params[displacement_reg_params["Model"] == "Storm_disp_abs"]["Dis Mag Value"].iloc[0],
                                        displacement_reg_params[displacement_reg_params["Model"] == "Storm_disp_abs"]["Duration"].iloc[0],
                                        displacement_reg_params[displacement_reg_params["Model"] == "Storm_disp_abs"]["Popdens"].iloc[0],
                                        displacement_reg_params[displacement_reg_params["Model"] == "Storm_disp_abs"]["Pop"].iloc[0]])
        
        self.storm_disp_pct_rmse = displacement_reg_params[displacement_reg_params["Model"] == "Storm_disp_pct"]["rmse"].iloc[0]
        self.storm_disp_pct = np.array([displacement_reg_params[displacement_reg_params["Model"] == "Storm_disp_pct"]["Intercept"].iloc[0],
                                        displacement_reg_params[displacement_reg_params["Model"] == "Storm_disp_pct"]["Dis Mag Value"].iloc[0],
                                        displacement_reg_params[displacement_reg_params["Model"] == "Storm_disp_pct"]["Duration"].iloc[0],
                                        displacement_reg_params[displacement_reg_params["Model"] == "Storm_disp_pct"]["Popdens"].iloc[0],0])
        # Create agents
        for i in range(len(countries)):
            a = CountryAgent(i, self)
            self.schedule.add(a)
        self.datacollector = mesa.DataCollector(
            agent_reporters={"idps":"idp",
                             "Floods":"flood_outcomes",
                              "Storms":"storm_outcomes",
                               "Population":"pop",
                                "GDP":"gdp",
                                 "Region":"region" },
            model_reporters={"Floods":flood_data,
                             "Storms":storm_data}
        )

    def step(self):
        """Advance the model by one step."""

        self.year += 1
        self.T = self.global_params[self.global_params["time"] == self.year]["T"].iloc[0]
        self.schedule.step()
        self.datacollector.collect(self)

In [612]:
scenarios = ["SSP119", "SSP126", "SSP245", "SSP370", "SSP585"]
start_year = 2020
end_year = 2300

results = {}

for scenario in scenarios:
    print("Running for ",scenario)
    results[scenario] = {}
    displacement_model = DisplacementModel(countries,scenario=scenario)
    for i in tqdm(range(start_year,end_year)):
        displacement_model.step()
    results[scenario]["model_data"] = displacement_model.datacollector.get_model_vars_dataframe()
    results[scenario]["country_data"] = displacement_model.datacollector.get_agent_vars_dataframe()
    results[scenario]["model_data"].to_csv("data/output/"+scenario+"/model_data.csv")
    results[scenario]["country_data"].to_csv("data/output/"+scenario+"/country_data.csv")


Running for  SSP119


100%|██████████| 280/280 [27:54<00:00,  5.98s/it] 


Running for  SSP126


100%|██████████| 280/280 [27:49<00:00,  5.96s/it]


Running for  SSP245


100%|██████████| 280/280 [33:14<00:00,  7.12s/it]


Running for  SSP370


100%|██████████| 280/280 [4:25:58<00:00, 57.00s/it]   


Running for  SSP585


100%|██████████| 280/280 [13:44:02<00:00, 176.58s/it]  


In [618]:
results[scenario]["country_data"] = displacement_model.datacollector.get_agent_vars_dataframe()

In [613]:
for (k,v) in results.items():
    v["model_data"]
    v["country_data"].to_csv("data/output/"+k+"country_data.csv")

In [619]:
results["SSP585"]["country_data"]

idps                                             Floods  \
Step AgentID                                                              
1    0             0  [[1.0, 71009.30334551958, 2.877302280394587, 1...   
     1             0  [[1.0, 231.25440004443226, 0.8474887743445298,...   
     2             0  [[1.0, 74.53177537719603, 1.6337235183272372, ...   
     3             0                                                 []   
     4             0  [[1.0, 2.873276058322517, 2.235084356653042, 5...   
...              ...                                                ...   
280  126           0                                                 []   
     127           0                                                 []   
     128      411001  [[1.0, 1180.469413912484, 0.7782090084178495, ...   
     129           0                                                 []   
     130           0                                                 []   

                                                         Storms  Population  \
Step AgentID                                                                  
1    0                                                       []   173164380   
     1                                                       []    11279239   
     2        [[1.0, 126.54775981071464, 0.4818441850165262,...    82400101   
     3                                                       []    47281172   
     4                                                       []    39062018   
...                                                         ...         ...   
280  126                                                     []     5115644   
     127                                                     []      721026   
     128                                                     []     4703671   
     129                                                     []    46169267   
     130                                                     []    11865601   

                       GDP           Region  
Step AgentID                                 
1    0        4.614680e+12    Southern Asia  
     1        3.037410e+12  Southern Europe  
     2        3.300841e+13   Western Europe  
     3        1.447695e+13  Southern Europe  
     4        6.289020e+11    Southern Asia  
...                    ...              ...  
280  126      2.045023e+13  Southern Europe  
     127      4.717572e+11  Southern Europe  
     128      8.065558e+12  Southern Europe  
     129      2.169985e+13     Western Asia  
     130      8.774926e+12     Western Asia  

[36680 rows x 6 columns]

In [620]:
last_step = results["SSP585"]["country_data"].index.get_level_values("Step").max()
results["SSP585"]["country_data"].xs(last_step, level="Step")["idps"].sum()

1877104749593699264

In [621]:
import plotly.express as px

In [622]:
country_data = results["SSP585"]["country_data"]

In [623]:
country_data.index = country_data.index.set_levels(countries,level="AgentID")
country_data.index = country_data.index.set_levels(displacement_model.country_params["time"].unique()+1,level="Step")

In [624]:
df = country_data.reset_index()
df = df.rename(columns={"AgentID":"Country"})

In [628]:
df["GDP"] = df["GDP"]/10

In [629]:
df["GDP_pc"] = df["GDP"] / df["Population"]

In [630]:
fig = px.scatter(df, x="GDP_pc", y="idps", animation_frame="Step", animation_group="Country",
           size="Population",color="Region", hover_name="Country",
           log_x=True,log_y=True, size_max=55, range_x=[100,10000000], range_y=[10000,1000000000000])

fig.update_layout(width=2000, height=1000)

In [585]:
df

Step Country    idps  \
0      2021     BGD       0   
1      2021     GRC       0   
2      2021     DEU       0   
3      2021     ESP       0   
4      2021     AFG  404750   
...     ...     ...     ...   
36675  2300     SVN    9644   
36676  2300     MNE     383   
36677  2300     SRB   76787   
36678  2300     ARE   37733   
36679  2300     QAT   28840   

                                                  Floods  \
0      [[1.0, 27495.744826908067, 0.8135679233102677,...   
1      [[1.0, 56806.58903949155, 1.7849769881740074, ...   
2      [[1.0, 153596.25574654783, 8.01335601110427, 2...   
3      [[1.0, 267835.7205085949, 0.7446312279873558, ...   
4      [[1.0, 57799.385112759075, 130.198827264357, 6...   
...                                                  ...   
36675                                                 []   
36676                                                 []   
36677  [[1.0, 76.41916017224139, 0.5232502189827729, ...   
36678  [[1.0, 89479.26959229476, 0.5781291024912547, ...   
36679                                                 []   

                                                  Storms  Population  \
0      [[1.0, 132.8262861512638, 0.5534109178956845, ...   171586771   
1      [[1.0, 88.22183971750033, 17.285615403899016, ...    11152137   
2      [[1.0, 153.4224256433102, 0.6768552308507566, ...    81344950   
3                                                     []    46699752   
4                                                     []    39204419   
...                                                  ...         ...   
36675                                                 []     1641233   
36676                                                 []      341798   
36677                                                 []     2783828   
36678                                                 []    16964949   
36679                                                 []     4575426   

                GDP           Region         GDP_pc  
0      4.572746e+11    Southern Asia    2664.975845  
1      2.980374e+11  Southern Europe   26724.689627  
2      3.235533e+12   Western Europe   39775.457481  
3      1.415208e+12  Southern Europe   30304.409325  
4      6.302360e+10    Southern Asia    1607.563678  
...             ...              ...            ...  
36675  4.106699e+11  Southern Europe  250220.361033  
36676  2.281739e+10  Southern Europe   66756.944306  
36677  3.714354e+11  Southern Europe  133426.148167  
36678  7.990992e+11     Western Asia   47102.954604  
36679  1.726975e+11     Western Asia   37744.580395  

[36680 rows x 9 columns]

In [588]:
model_data

Floods                            Storms
0     {'Num': 858, 'idps': 7474732.0}   {'Num': 414, 'idps': 4656049.0}
1    {'Num': 786, 'idps': 10990994.0}  {'Num': 354, 'idps': 10402455.0}
2    {'Num': 738, 'idps': 10007213.0}  {'Num': 336, 'idps': 14982804.0}
3     {'Num': 630, 'idps': 4388945.0}  {'Num': 402, 'idps': 29063710.0}
4     {'Num': 672, 'idps': 3849616.0}  {'Num': 438, 'idps': 22826259.0}
..                                ...                               ...
275   {'Num': 720, 'idps': 2531840.0}   {'Num': 318, 'idps': 2428105.0}
276   {'Num': 738, 'idps': 3485696.0}   {'Num': 360, 'idps': 1534189.0}
277   {'Num': 666, 'idps': 2837605.0}   {'Num': 396, 'idps': 8106371.0}
278   {'Num': 618, 'idps': 1700456.0}      {'Num': 330, 'idps': 1159.0}
279   {'Num': 792, 'idps': 1065572.0}    {'Num': 378, 'idps': 147140.0}

[280 rows x 2 columns]